## Env

In [1]:
!pip install lightning

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 819.0/819.0 kB 46.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 3.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 104.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 99.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 52.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 5.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 21.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 7.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 5.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 45.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 962.5/962.5 kB 52.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

In [2]:
from google.colab import drive
drive.mount("/content/drive/")

Mounted at /content/drive/


In [3]:
!unzip -qq "/content/drive/MyDrive/MAGISTERKA/datasets/fog-combined.zip" -d "/content/datasets/"

## Setup

In [4]:
from pathlib import Path
from time import time

import lightning as L
from lightning.pytorch.loggers import TensorBoardLogger

import torch
from torchvision.models import get_weight
from torchvision.transforms import v2

In [5]:
base_transform = v2.Compose([
    v2.Resize((256, 256), v2.InterpolationMode.BILINEAR),
    v2.CenterCrop((224, 224)),
    v2.ToImage(),
    v2.ToDtype(torch.float32, scale=True),
])
transforms = {
    "grayscale": v2.Compose([
        base_transform,
        v2.Grayscale(num_output_channels=3)
    ]),
    "color": v2.Compose([
        base_transform,
    ]),
}

In [6]:
BASE_PATH = Path("/content")
DRIVE_PATH = Path("/content/drive/MyDrive/MAGISTERKA")
SAVE_DIR = DRIVE_PATH / "lightning_logs/runs/classify"

In [7]:
import sys
sys.path.insert(0, str(DRIVE_PATH / 'src'))
from cnn_model import CNNClassifier, get_dataloader

In [8]:
DATASET_PATHS = {
    'fog-detection': BASE_PATH / 'datasets/fog-detection-dataset-prepared',
    'fog-or-smog': BASE_PATH / 'datasets/fog-or-smog-detection-dataset-prepared',
    'foggy-cityscapes': BASE_PATH / 'datasets/foggy-cityscapes-image-dataset-prepared',
    'combined': BASE_PATH / 'datasets/fog-combined',
}

In [9]:
DATASET_NORMALIZATION = {
    'fog-detection': {'mean': [0.4850, 0.5044, 0.4878], 'std': [0.2631, 0.2524, 0.2793]},
    'fog-or-smog': {'mean': [0.5411, 0.5339, 0.5088], 'std': [0.2353, 0.2157, 0.2289]},
    'foggy-cityscapes': {'mean': [0.4169, 0.4507, 0.4173], 'std': [0.1860, 0.1835, 0.1820]},
    'combined': {'mean': [0.5017, 0.5087, 0.4826], 'std': [0.2259, 0.2118, 0.2227]}
}

In [10]:
def get_dataset_stats(dataset_path: Path):
  dataset = get_dataloader(dataset_path, transforms["color"])
  # Calculate mean color and std
  mean = torch.zeros(3)
  std = torch.zeros(3)

  for images, _ in dataset:
    mean += images.mean(dim=(0, 2, 3))
    std += images.std(dim=(0, 2, 3))

  mean /= len(dataset)
  std /= len(dataset)

  return mean, std


In [11]:
# get_dataset_stats(DATASET_PATHS['fog-detection'])

In [12]:
# get_dataset_stats(DATASET_PATHS['fog-or-smog'])

In [13]:
# get_dataset_stats(DATASET_PATHS['foggy-cityscapes'])

In [14]:
# get_dataset_stats(DATASET_PATHS['combined'])

In [15]:
def _get_formatted_metric(values: list[float]):
  avg = sum(values) / len(values)
  std = (sum([(v - avg) ** 2 for v in values]) / len(values)) ** 0.5
  return f"{avg:.4f} ± {std:.4f}"

def run_model(
    run_name: str,
    model_name: str,
    dataset: str,
    version: int = 1,
    repeat: int = 5,
    transform: str = "color",
    normalize: bool = False
):
  save_dir = SAVE_DIR / run_name
  model = CNNClassifier(
      model_name=model_name,
      num_classes=2,
      weights=False,
  )
  _transform = transforms[transform]
  if normalize:
    _transform = v2.Compose([
        base_transform,
        v2.Normalize(**DATASET_NORMALIZATION[dataset])
    ])

  train_dataloaders=get_dataloader(
    path=DATASET_PATHS[dataset] / "train",
    transform=_transform,
    batch_size=32,
    shuffle=True,
    num_workers=2,
  )
  val_dataloaders=get_dataloader(
    path=DATASET_PATHS[dataset] / "val",
    transform=_transform,
    batch_size=32,
    shuffle=False,
    num_workers=2,
  )

  test_dataloader = {
      dataset_name: get_dataloader(path=path / "test", transform=_transform)
      for dataset_name, path in DATASET_PATHS.items()
  }

  final_res = {}
  training_times = []
  for i in range(repeat):
    trainer = L.Trainer(
        max_epochs=20,
        logger=L.pytorch.loggers.TensorBoardLogger(
            save_dir=save_dir,
            name=f"{model_name}-{dataset}-{transform}-{normalize}",
            version=f"{version}000{i+1:02}",
        ),
        callbacks=[
            L.pytorch.callbacks.early_stopping.EarlyStopping(
                monitor="val_loss", mode="min", patience=5, verbose=False
            ),
            L.pytorch.callbacks.ModelCheckpoint(
                monitor="val_f1",
                mode="max",
                dirpath=save_dir / f"{model_name}-{dataset}" / f"version_{version}",
                filename=f"{model_name}-{dataset}-{transform}-{normalize}",
            ),
        ],
        log_every_n_steps=1,
    )

    model = CNNClassifier(
      model_name=model_name,
      num_classes=2,
      weights=False,
    )
    _start = time()
    trainer.fit(
        model,
        train_dataloaders=train_dataloaders,
        val_dataloaders=val_dataloaders
    )
    _end = time()
    training_times.append(_end - _start)
    res = {
        dataset_name: trainer.test(
            model,  dataloader
        )[0]
        for dataset_name, dataloader in test_dataloader.items()
    }
    for dataset_name, metrics in res.items():
      if dataset_name not in final_res:
        final_res[dataset_name] = {}
      for metric_name, metric_value in metrics.items():
        if metric_name not in final_res[dataset_name]:
          final_res[dataset_name][metric_name] = []
        final_res[dataset_name][metric_name].append(metric_value)


  latex_table = [
    [
      dataset,
      # *[round(m, 4) for m in metrics.values()]
      # Add average value and std
      *[_get_formatted_metric(m) for m in metrics.values()]
    ] for dataset, metrics in final_res.items()
  ]
  latex_table_str = ""
  for line in latex_table:
    latex_table_str += " & ".join([str(l) for l in line]) + " \\\\\n"
  return latex_table_str


## ResNet18

In [ ]:
run_model(
  run_name="CNN-COLOR-TRUE",
  model_name="ResNet18",
  dataset='combined',
  version=1,
  transform='color',
  normalize=True
)

/usr/local/lib/python3.11/dist-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=None`.
  warnings.warn(msg)
INFO: GPU available: True (cuda), used: True
INFO:lightning.pytorch.utilities.rank_zero:GPU available: True (cuda), used: True
INFO: TPU available: False, using: 0 TPU cores
INFO:lightning.pytorch.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO: HPU available: False, using: 0 HPUs
INFO:lightning.pytorch.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO: 
  | Name               | Type             | Params | Mode 
----------------------------------------------------------------
0 | model              | ResNet           | 11.2 M | train
1 | criteri

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

...

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃        Test metric        ┃       DataLoader 0        ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│       test_accuracy       │    0.8232323527336121     │
│          test_f1          │    0.8444444537162781     │
│      test_precision       │    0.7539682388305664     │
│        test_recall        │    0.9595959782600403     │
└───────────────────────────┴───────────────────────────┘

INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Testing: |          | 0/? [00:00<?, ?it/s]

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃        Test metric        ┃       DataLoader 0        ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│       test_accuracy       │    0.9361979365348816     │
│          test_f1          │    0.9411764740943909     │
│      test_precision       │    0.9137529134750366     │
│        test_recall        │    0.9702970385551453     │
└───────────────────────────┴───────────────────────────┘

'fog-detection & 0.9811 ± 0.0215 & 0.9845 ± 0.0176 & 0.9877 ± 0.0179 & 0.9815 ± 0.0226 \\\\\nfog-or-smog & 0.9733 ± 0.0029 & 0.9738 ± 0.0029 & 0.9864 ± 0.0049 & 0.9617 ± 0.0061 \\\\\nfoggy-cityscapes & 0.8596 ± 0.0233 & 0.8603 ± 0.0188 & 0.8647 ± 0.0554 & 0.8626 ± 0.0566 \\\\\ncombined & 0.9451 ± 0.0060 & 0.9474 ± 0.0052 & 0.9551 ± 0.0211 & 0.9406 ± 0.0174 \\\\\n'

In [ ]:
run_model(
  run_name="CNN-COLOR-FALSE",
  model_name="ResNet18",
  dataset='combined',
  version=1,
  transform='color',
  normalize=False
)

/usr/local/lib/python3.11/dist-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=None`.
  warnings.warn(msg)
INFO: GPU available: True (cuda), used: True
INFO:lightning.pytorch.utilities.rank_zero:GPU available: True (cuda), used: True
INFO: TPU available: False, using: 0 TPU cores
INFO:lightning.pytorch.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO: HPU available: False, using: 0 HPUs
INFO:lightning.pytorch.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO: 
  | Name               | Type             | Params | Mode 
----------------------------------------------------------------
0 | model              | ResNet           | 11.2 M | train
1 | criteri

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

...

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃        Test metric        ┃       DataLoader 0        ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│       test_accuracy       │    0.8232323527336121     │
│          test_f1          │    0.7904191613197327     │
│      test_precision       │     0.970588207244873     │
│        test_recall        │    0.6666666865348816     │
└───────────────────────────┴───────────────────────────┘

INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Testing: |          | 0/? [00:00<?, ?it/s]

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃        Test metric        ┃       DataLoader 0        ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│       test_accuracy       │        0.93359375         │
│          test_f1          │    0.9341935515403748     │
│      test_precision       │    0.9757412672042847     │
│        test_recall        │     0.896039605140686     │
└───────────────────────────┴───────────────────────────┘

'fog-detection & 0.9774 ± 0.0228 & 0.9817 ± 0.0184 & 0.9759 ± 0.0226 & 0.9877 ± 0.0179 \\\\\nfog-or-smog & 0.9668 ± 0.0026 & 0.9677 ± 0.0026 & 0.9739 ± 0.0053 & 0.9617 ± 0.0081 \\\\\nfoggy-cityscapes & 0.8303 ± 0.0216 & 0.8194 ± 0.0413 & 0.8749 ± 0.0758 & 0.7939 ± 0.1326 \\\\\ncombined & 0.9331 ± 0.0051 & 0.9355 ± 0.0066 & 0.9484 ± 0.0257 & 0.9248 ± 0.0349 \\\\\n'

In [ ]:
run_model(
  run_name="CNN-GRAYSCALE-TRUE",
  model_name="ResNet18",
  dataset='combined',
  version=1,
  transform='grayscale',
  normalize=True
)

/usr/local/lib/python3.11/dist-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=None`.
  warnings.warn(msg)
INFO: GPU available: True (cuda), used: True
INFO:lightning.pytorch.utilities.rank_zero:GPU available: True (cuda), used: True
INFO: TPU available: False, using: 0 TPU cores
INFO:lightning.pytorch.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO: HPU available: False, using: 0 HPUs
INFO:lightning.pytorch.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO: 
  | Name               | Type             | Params | Mode 
----------------------------------------------------------------
0 | model              | ResNet           | 11.2 M | train
1 | criteri

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

...

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃        Test metric        ┃       DataLoader 0        ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│       test_accuracy       │    0.8888888955116272     │
│          test_f1          │    0.8877550959587097     │
│      test_precision       │    0.8969072103500366     │
│        test_recall        │    0.8787878751754761     │
└───────────────────────────┴───────────────────────────┘

INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Testing: |          | 0/? [00:00<?, ?it/s]

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃        Test metric        ┃       DataLoader 0        ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│       test_accuracy       │         0.953125          │
│          test_f1          │    0.9549999833106995     │
│      test_precision       │    0.9646464586257935     │
│        test_recall        │    0.9455445408821106     │
└───────────────────────────┴───────────────────────────┘

'fog-detection & 0.9868 ± 0.0128 & 0.9894 ± 0.0101 & 0.9793 ± 0.0195 & 1.0000 ± 0.0000 \\\\\nfog-or-smog & 0.9716 ± 0.0046 & 0.9721 ± 0.0046 & 0.9846 ± 0.0034 & 0.9600 ± 0.0086 \\\\\nfoggy-cityscapes & 0.8505 ± 0.0316 & 0.8437 ± 0.0412 & 0.8752 ± 0.0232 & 0.8202 ± 0.0863 \\\\\ncombined & 0.9424 ± 0.0093 & 0.9444 ± 0.0098 & 0.9575 ± 0.0086 & 0.9322 ± 0.0241 \\\\\n'

In [16]:
run_model(
  run_name="CNN-GRAYSCALE-FALSE",
  model_name="ResNet18",
  dataset='combined',
  version=1,
  transform='grayscale',
  normalize=False
)

/usr/local/lib/python3.11/dist-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=None`.
  warnings.warn(msg)
INFO: GPU available: True (cuda), used: True
INFO:lightning.pytorch.utilities.rank_zero:GPU available: True (cuda), used: True
INFO: TPU available: False, using: 0 TPU cores
INFO:lightning.pytorch.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO: HPU available: False, using: 0 HPUs
INFO:lightning.pytorch.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO: 
  | Name               | Type             | Params | Mode 
----------------------------------------------------------------
0 | model              | ResNet           | 11.2 M | train
1 | criteri

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

...

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃        Test metric        ┃       DataLoader 0        ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│       test_accuracy       │    0.8888888955116272     │
│          test_f1          │    0.8877550959587097     │
│      test_precision       │    0.8969072103500366     │
│        test_recall        │    0.8787878751754761     │
└───────────────────────────┴───────────────────────────┘

INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Testing: |          | 0/? [00:00<?, ?it/s]

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃        Test metric        ┃       DataLoader 0        ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│       test_accuracy       │    0.8932291865348816     │
│          test_f1          │    0.9035294055938721     │
│      test_precision       │    0.8609865307807922     │
│        test_recall        │    0.9504950642585754     │
└───────────────────────────┴───────────────────────────┘

'fog-detection & 0.9396 ± 0.0250 & 0.9519 ± 0.0193 & 0.9374 ± 0.0430 & 0.9692 ± 0.0323 \\\\\nfog-or-smog & 0.9267 ± 0.0190 & 0.9289 ± 0.0152 & 0.9425 ± 0.0510 & 0.9192 ± 0.0321 \\\\\nfoggy-cityscapes & 0.8485 ± 0.0361 & 0.8429 ± 0.0456 & 0.8681 ± 0.0318 & 0.8242 ± 0.0802 \\\\\ncombined & 0.9083 ± 0.0140 & 0.9119 ± 0.0140 & 0.9231 ± 0.0355 & 0.9040 ± 0.0409 \\\\\n'

## Swin_S

In [17]:
run_model(
  run_name="CNN-COLOR-TRUE",
  model_name="Swin_S",
  dataset='combined',
  version=1,
  transform='color',
  normalize=True
)

/usr/local/lib/python3.11/dist-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=None`.
  warnings.warn(msg)
INFO: GPU available: True (cuda), used: True
INFO:lightning.pytorch.utilities.rank_zero:GPU available: True (cuda), used: True
INFO: TPU available: False, using: 0 TPU cores
INFO:lightning.pytorch.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO: HPU available: False, using: 0 HPUs
INFO:lightning.pytorch.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO: 
  | Name               | Type             | Params | Mode 
----------------------------------------------------------------
0 | model              | SwinTransformer  | 48.8 M | train
1 | criteri

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

...

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃        Test metric        ┃       DataLoader 0        ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│       test_accuracy       │     0.808080792427063     │
│          test_f1          │     0.822429895401001     │
│      test_precision       │    0.7652173638343811     │
│        test_recall        │    0.8888888955116272     │
└───────────────────────────┴───────────────────────────┘

INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Testing: |          | 0/? [00:00<?, ?it/s]

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃        Test metric        ┃       DataLoader 0        ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│       test_accuracy       │    0.9153645634651184     │
│          test_f1          │    0.9212121367454529     │
│      test_precision       │    0.9026128053665161     │
│        test_recall        │    0.9405940771102905     │
└───────────────────────────┴───────────────────────────┘

'fog-detection & 0.9585 ± 0.0335 & 0.9656 ± 0.0281 & 0.9717 ± 0.0190 & 0.9600 ± 0.0396 \\\\\nfog-or-smog & 0.9504 ± 0.0113 & 0.9528 ± 0.0104 & 0.9403 ± 0.0181 & 0.9658 ± 0.0072 \\\\\nfoggy-cityscapes & 0.8343 ± 0.0161 & 0.8387 ± 0.0133 & 0.8200 ± 0.0339 & 0.8606 ± 0.0334 \\\\\ncombined & 0.9216 ± 0.0081 & 0.9265 ± 0.0073 & 0.9145 ± 0.0137 & 0.9391 ± 0.0107 \\\\\n'

In [18]:
run_model(
  run_name="CNN-COLOR-FALSE",
  model_name="Swin_S",
  dataset='combined',
  version=1,
  transform='color',
  normalize=False
)

/usr/local/lib/python3.11/dist-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=None`.
  warnings.warn(msg)
INFO: GPU available: True (cuda), used: True
INFO:lightning.pytorch.utilities.rank_zero:GPU available: True (cuda), used: True
INFO: TPU available: False, using: 0 TPU cores
INFO:lightning.pytorch.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO: HPU available: False, using: 0 HPUs
INFO:lightning.pytorch.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO: 
  | Name               | Type             | Params | Mode 
----------------------------------------------------------------
0 | model              | SwinTransformer  | 48.8 M | train
1 | criteri

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

...

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃        Test metric        ┃       DataLoader 0        ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│       test_accuracy       │     0.747474730014801     │
│          test_f1          │    0.7159090638160706     │
│      test_precision       │    0.8181818127632141     │
│        test_recall        │    0.6363636255264282     │
└───────────────────────────┴───────────────────────────┘

INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Testing: |          | 0/? [00:00<?, ?it/s]

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃        Test metric        ┃       DataLoader 0        ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│       test_accuracy       │        0.90234375         │
│          test_f1          │    0.9029754400253296     │
│      test_precision       │    0.9457994699478149     │
│        test_recall        │    0.8638613820075989     │
└───────────────────────────┴───────────────────────────┘

'fog-detection & 0.8981 ± 0.0817 & 0.9065 ± 0.0833 & 0.9764 ± 0.0259 & 0.8523 ± 0.1202 \\\\\nfog-or-smog & 0.9513 ± 0.0152 & 0.9529 ± 0.0133 & 0.9610 ± 0.0339 & 0.9458 ± 0.0105 \\\\\nfoggy-cityscapes & 0.7687 ± 0.0564 & 0.7773 ± 0.0474 & 0.7686 ± 0.0888 & 0.8121 ± 0.1223 \\\\\ncombined & 0.8969 ± 0.0333 & 0.9024 ± 0.0277 & 0.9094 ± 0.0564 & 0.8980 ± 0.0238 \\\\\n'

In [19]:
run_model(
  run_name="CNN-GRAYSCALE-TRUE",
  model_name="Swin_S",
  dataset='combined',
  version=1,
  transform='grayscale',
  normalize=True
)

/usr/local/lib/python3.11/dist-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=None`.
  warnings.warn(msg)
INFO: GPU available: True (cuda), used: True
INFO:lightning.pytorch.utilities.rank_zero:GPU available: True (cuda), used: True
INFO: TPU available: False, using: 0 TPU cores
INFO:lightning.pytorch.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO: HPU available: False, using: 0 HPUs
INFO:lightning.pytorch.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO: 
  | Name               | Type             | Params | Mode 
----------------------------------------------------------------
0 | model              | SwinTransformer  | 48.8 M | train
1 | criteri

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

...

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃        Test metric        ┃       DataLoader 0        ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│       test_accuracy       │    0.8181818127632141     │
│          test_f1          │    0.7906976938247681     │
│      test_precision       │     0.931506872177124     │
│        test_recall        │    0.6868686676025391     │
└───────────────────────────┴───────────────────────────┘

INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Testing: |          | 0/? [00:00<?, ?it/s]

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃        Test metric        ┃       DataLoader 0        ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│       test_accuracy       │    0.9192708134651184     │
│          test_f1          │    0.9196891188621521     │
│      test_precision       │    0.9646739363670349     │
│        test_recall        │    0.8787128925323486     │
└───────────────────────────┴───────────────────────────┘

'fog-detection & 0.9679 ± 0.0243 & 0.9735 ± 0.0199 & 0.9847 ± 0.0238 & 0.9631 ± 0.0250 \\\\\nfog-or-smog & 0.9599 ± 0.0099 & 0.9609 ± 0.0097 & 0.9704 ± 0.0131 & 0.9517 ± 0.0146 \\\\\nfoggy-cityscapes & 0.8222 ± 0.0290 & 0.8158 ± 0.0302 & 0.8598 ± 0.0816 & 0.7939 ± 0.1007 \\\\\ncombined & 0.9255 ± 0.0137 & 0.9282 ± 0.0127 & 0.9440 ± 0.0330 & 0.9149 ± 0.0333 \\\\\n'

In [20]:
run_model(
  run_name="CNN-GRAYSCALE-FALSE",
  model_name="Swin_S",
  dataset='combined',
  version=1,
  transform='grayscale',
  normalize=False
)

/usr/local/lib/python3.11/dist-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=None`.
  warnings.warn(msg)
INFO: GPU available: True (cuda), used: True
INFO:lightning.pytorch.utilities.rank_zero:GPU available: True (cuda), used: True
INFO: TPU available: False, using: 0 TPU cores
INFO:lightning.pytorch.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO: HPU available: False, using: 0 HPUs
INFO:lightning.pytorch.utilities.rank_zero:HPU available: False, using: 0 HPUs
/usr/local/lib/python3.11/dist-packages/lightning/pytorch/callbacks/model_checkpoint.py:654: Checkpoint directory /content/drive/MyDrive/MAGISTERKA/lightning_logs/runs/classify/CNN-GRAYSCALE-FALSE/Swin_S-combined/version_1 exists and is not empty.
INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

...

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

INFO: 
Detected KeyboardInterrupt, attempting graceful shutdown ...
INFO:lightning.pytorch.utilities.rank_zero:
Detected KeyboardInterrupt, attempting graceful shutdown ...
Exception ignored in: <function PluginV3.__del__ at 0x7d70519bcea0>
Traceback (most recent call last):
  File "/usr/local/lib/python3.11/dist-packages/imageio/core/v3_plugin_api.py", line 370, in __del__
    self.close()
  File "/usr/local/lib/python3.11/dist-packages/imageio/plugins/pillow.py", line 144, in close
    self._flush_writer()
  File "/usr/local/lib/python3.11/dist-packages/imageio/plugins/pillow.py", line 476, in _flush_writer
    if len(self.images_to_write) == 0:
           ^^^^^^^^^^^^^^^^^^^^
AttributeError: 'PillowPlugin' object has no attribute 'images_to_write'


NameError: name 'exit' is not defined

## EfficientNet B1

In [ ]:
run_model(
  run_name="CNN-COLOR-TRUE",
  model_name="EfficientNet_B1",
  dataset='combined',
  version=1,
  transform='color',
  normalize=True
)

In [ ]:
run_model(
  run_name="CNN-COLOR-FALSE",
  model_name="EfficientNet_B1",
  dataset='combined',
  version=1,
  transform='color',
  normalize=False
)

In [ ]:
run_model(
  run_name="CNN-GRAYSCALE-TRUE",
  model_name="EfficientNet_B1",
  dataset='combined',
  version=1,
  transform='grayscale',
  normalize=True
)

In [ ]:
run_model(
  run_name="CNN-GRAYSCALE-FALSE",
  model_name="EfficientNet_B1",
  dataset='combined',
  version=1,
  transform='grayscale',
  normalize=False
)